<a href="https://colab.research.google.com/github/gabilodeau/INF6804/blob/master/Reconnaissance_d'activites.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# INF6804 Vision par ordinateur
Polytechnique Montréal <br>
Auteur : Mehdi Miah

Description : ce Jupyter notebook implémente un algorithme de reconnaissance d'activités. L'entrée est une vidéo et la sortie est composée de $n$ probabilités associées à $n$ activités (ici, $n=400$). Ce notebook repose sur la librairie MMAction du MMLab.

## Installation des librairies

Après cette première cellule, il faut cliquer sur "Redémarrer la session", puis continuez avec les cellules suivantes.


In [1]:
# MMAction
!git clone https://github.com/open-mmlab/mmaction2.git  # 1.2.0, commit 4d6c934
%cd mmaction2
%pip install -v -e .

# Timm (PyTorch Image Models)
%pip install timm==1.0.9

# Openmim (OpenMMLab packages)
!pip3 install openmim==0.3.9

Cloning into 'mmaction2'...
remote: Enumerating objects: 22864, done.
remote: Total 22864 (delta 0), reused 0 (delta 0), pack-reused 22864 (from 1)
Receiving objects: 100% (22864/22864), 69.62 MiB | 6.61 MiB/s, done.
Resolving deltas: 100% (16120/16120), done.
/content/mmaction2
Using pip 24.1.2 from /usr/local/lib/python3.10/dist-packages/pip (python 3.10)
Obtaining file:///content/mmaction2
  Running command python setup.py egg_info
  running egg_info
  creating /tmp/pip-pip-egg-info-vbjtjnw3/mmaction2.egg-info
  writing /tmp/pip-pip-egg-info-vbjtjnw3/mmaction2.egg-info/PKG-INFO
  writing dependency_links to /tmp/pip-pip-egg-info-vbjtjnw3/mmaction2.egg-info/dependency_links.txt
  writing requirements to /tmp/pip-pip-egg-info-vbjtjnw3/mmaction2.egg-info/requires.txt
  writing top-level names to /tmp/pip-pip-egg-info-vbjtjnw3/mmaction2.egg-info/top_level.txt
  writing manifest file '/tmp/pip-pip-egg-info-vbjtjnw3/mmaction2.egg-info/SOURCES.txt'
  reading manifest file '/tmp/pip-pip-egg

Cliquez sur "Redémarrer la session", puis continuez avec la cellule ci-dessous


In [1]:
# MMEngine (Engine of OpenMMLab projects)
!mim install mmengine==0.10.4

# Previous version of torch : for mmcv compatibility
%pip install torch==2.1.0 torchvision==0.16.0 --index-url https://download.pytorch.org/whl/cu121

# MMCV (OpenMMLab Computer Vision Foundation)
!mim install mmcv==2.1.0

# Import librairies
from IPython.display import display, HTML, Video

from mmaction.apis import init_recognizer, inference_recognizer

Looking in links: https://download.openmmlab.com/mmcv/dist/cu121/torch2.4.0/index.html
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.4/45.4 kB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 451.7/451.7 kB 30.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 254.7/254.7 kB 23.6 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
mmaction2 1.2.0 requires mmcv<2.2.0,>=2.0.0rc4, which is not installed.
Looking in indexes: https://download.pytorch.org/whl/cu121
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 GB 551.4 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 88.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.2/89.2 MB 9.6 MB/s eta 0:00:00
  Attempting uninstall: torch
    Found existing installation: torch 2.4.0+cu121
    Uninstalling torch-2.4.0+cu121:
      Suc

## Téléchargement de vidéos

Pour illustrer la reconnaissance d'activité, téléchargeons d'abord quelques vidéos et affichons les.

In [2]:
%cd /content

# Ice hockey
!wget https://videos.pexels.com/video-files/8970119/8970119-sd_640_338_25fps.mp4 -P /content/

# Ballet dancer
!wget https://videos.pexels.com/video-files/5051387/5051387-sd_640_360_25fps.mp4 -P /content/

# Making desserts
!wget https://videos.pexels.com/video-files/4109927/4109927-sd_640_360_30fps.mp4 -P /content/

/content
--2024-09-18 15:37:38--  https://videos.pexels.com/video-files/8970119/8970119-sd_640_338_25fps.mp4
Resolving videos.pexels.com (videos.pexels.com)... 104.18.67.220, 104.18.66.220, 2606:4700::6812:43dc, ...
Connecting to videos.pexels.com (videos.pexels.com)|104.18.67.220|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1377081 (1.3M)
Saving to: ‘/content/8970119-sd_640_338_25fps.mp4’

8970119-sd_640_338_ 100%[===================>]   1.31M  6.93MB/s    in 0.2s    

2024-09-18 15:37:39 (6.93 MB/s) - ‘/content/8970119-sd_640_338_25fps.mp4’ saved [1377081/1377081]

--2024-09-18 15:37:39--  https://videos.pexels.com/video-files/5051387/5051387-sd_640_360_25fps.mp4
Resolving videos.pexels.com (videos.pexels.com)... 104.18.67.220, 104.18.66.220, 2606:4700::6812:43dc, ...
Connecting to videos.pexels.com (videos.pexels.com)|104.18.67.220|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1434563 (1.4M)
Saving to: ‘/content/5051387-sd_640

In [3]:
# Paths to the videos
video_paths = ['8970119-sd_640_338_25fps.mp4', '5051387-sd_640_360_25fps.mp4', '4109927-sd_640_360_30fps.mp4']

# Create video widgets
videos = [Video(video_path, width=400, embed=True) for video_path in video_paths]

# Function to display videos side by side
def display_videos_side_by_side(videos):
    video_html = ''.join([f'<div style="display:inline-block; margin:10px;">{video._repr_html_()}</div>' for video in videos])
    display(HTML(video_html))

# Display videos side by side
display_videos_side_by_side(videos)

## Chargement du modèle de reconnaissance d'activité

Listons quelques des 400 activités reconnaissables.

In [4]:
# File listing the 400 activities
label_file = './mmaction2/tools/data/kinetics/label_map_k400.txt'
labels = open(label_file).readlines()
labels = [x.strip() for x in labels]

# Examples of activities
print(f"Les 10 premiers activités : {labels[:10]}")

Les 10 premiers activités : ['abseiling', 'air drumming', 'answering questions', 'applauding', 'applying cream', 'archery', 'arm wrestling', 'arranging flowers', 'assembling computer', 'auctioning']


Cinq modèles sont proposés dans ce notebook (voir références pour plus d'infos):
- TSN ([Temporal Segment Networks: Towards Good Practices for Deep Action Recognition](https://arxiv.org/pdf/1608.00859), ECCV 2016) ;
- CSN ([Video Classification with Channel-Separated Convolutional Networks](https://openaccess.thecvf.com/content_ICCV_2019/papers/Tran_Video_Classification_With_Channel-Separated_Convolutional_Networks_ICCV_2019_paper.pdf), ICCV 2019) ;
- SlowFast ([SlowFast Networks for Video Recognition](https://openaccess.thecvf.com/content_ICCV_2019/papers/Feichtenhofer_SlowFast_Networks_for_Video_Recognition_ICCV_2019_paper.pdf), ICCV 2019) ;
- VideoSwin ([Video Swin Transformer](https://openaccess.thecvf.com/content/CVPR2022/papers/Liu_Video_Swin_Transformer_CVPR_2022_paper.pdf), CVPR 2022) ;
- VideoMAE v2 ([VideoMAE V2: Scaling Video Masked Autoencoders with Dual Masking](https://openaccess.thecvf.com/content/CVPR2023/papers/Wang_VideoMAE_V2_Scaling_Video_Masked_Autoencoders_With_Dual_Masking_CVPR_2023_paper.pdf), CVPR 2023) ;



In [5]:
# Dictionnary of some models
dict_model = {'TSN-ResNet50-1x1x8': {'config_file': './mmaction2/configs/recognition/tsn/tsn_imagenet-pretrained-r50_8xb32-1x1x8-100e_kinetics400-rgb.py',
                                     'checkpoint_file': 'https://download.openmmlab.com/mmaction/v1.0/recognition/tsn/tsn_imagenet-pretrained-r50_8xb32-1x1x8-100e_kinetics400-rgb/tsn_imagenet-pretrained-r50_8xb32-1x1x8-100e_kinetics400-rgb_20220906-2692d16c.pth'},
              'CSN-ResNet152-pretrained': {'config_file': './mmaction2/configs/recognition/csn/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb.py',
                                           'checkpoint_file': 'https://download.openmmlab.com/mmaction/v1.0/recognition/csn/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb_20220811-c7a3cc5b.pth'},
              'SlowFast-ResNet101': {'config_file': './mmaction2/configs/recognition/slowfast/slowfast_r101_8xb8-8x8x1-256e_kinetics400-rgb.py',
                                           'checkpoint_file': 'https://download.openmmlab.com/mmaction/v1.0/recognition/slowfast/slowfast_r101_8xb8-8x8x1-256e_kinetics400-rgb/slowfast_r101_8xb8-8x8x1-256e_kinetics400-rgb_20220818-9c0e09bd.pth'},
              'VideoSwin-T': {'config_file': './mmaction2/configs/recognition/swin/swin-tiny-p244-w877_in1k-pre_8xb8-amp-32x2x1-30e_kinetics400-rgb.py',
                                           'checkpoint_file': 'https://download.openmmlab.com/mmaction/v1.0/recognition/swin/swin-tiny-p244-w877_in1k-pre_8xb8-amp-32x2x1-30e_kinetics400-rgb/swin-tiny-p244-w877_in1k-pre_8xb8-amp-32x2x1-30e_kinetics400-rgb_20220930-241016b2.pth'},
              'VideoMAEv2-S': {'config_file': './mmaction2/configs/recognition/videomaev2/vit-small-p16_videomaev2-vit-g-dist-k710-pre_16x4x1_kinetics-400.py',
                                           'checkpoint_file': 'https://download.openmmlab.com/mmaction/v1.0/recognition/videomaev2/vit-small-p16_videomaev2-vit-g-dist-k710-pre_16x4x1_kinetics-400/vit-small-p16_videomaev2-vit-g-dist-k710-pre_16x4x1_kinetics-400_20230510-25c748fd.pth'},
              }

In [6]:
# Selection of a model
#model_name = 'TSN-ResNet50-1x1x8'
model_name = 'CSN-ResNet152-pretrained'
#model_name = 'SlowFast-ResNet101'
#model_name = 'VideoSwin-T'
#model_name = 'VideoMAEv2-S'

# Load the selected model
model = init_recognizer(config=dict_model[model_name]['config_file'],
                        checkpoint=dict_model[model_name]['checkpoint_file'],
                        device='cuda:0')

Loads checkpoint by http backend from path: https://download.openmmlab.com/mmaction/v1.0/recognition/csn/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb_20220811-c7a3cc5b.pth


Downloading: "https://download.openmmlab.com/mmaction/v1.0/recognition/csn/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb_20220811-c7a3cc5b.pth" to /root/.cache/torch/hub/checkpoints/ircsn_ig65m-pretrained-r152_8xb12-32x2x1-58e_kinetics400-rgb_20220811-c7a3cc5b.pth


## Prédictions

Pour chaque vidéo, le modèle sélectionné prédit une probabilité pour chacune des 400 activités reconnaissables. Ci-dessous, seules les cinq plus probables sont affichées.

In [7]:
print(f"Prédictions avec le modèle {model_name} :")

for videoname in video_paths:

  # Prediction
  pred_result = inference_recognizer(model, videoname)

  # Get the 5 top scores
  pred_scores = pred_result.pred_score.tolist()
  score_tuples = tuple(zip(range(len(pred_scores)), pred_scores))
  score_sorted = sorted(score_tuples, key=lambda x: x[1], reverse=True)
  top5_label = score_sorted[:5]
  results = [(labels[k[0]], k[1]) for k in top5_label]

  print(f"\ntop-5 activités pour la vidéo : {videoname}\n")
  for res in results:
      print(f'\t{res[0] :<40s} {res[1]:7.2%}')



Prédictions avec le modèle CSN-ResNet152-pretrained :
09/18 15:37:55 - mmengine - WARNING - "FileClient" will be deprecated in future. Please use io functions in https://mmengine.readthedocs.io/en/latest/api/fileio.html#file-io
09/18 15:37:55 - mmengine - WARNING - "HardDiskBackend" is the alias of "LocalBackend" and the former will be deprecated in future.

top-5 activités pour la vidéo : 8970119-sd_640_338_25fps.mp4

	playing ice hockey                        83.93%
	hockey stop                               12.63%
	ice skating                                2.77%
	pumping fist                               0.23%
	shaking hands                              0.08%

top-5 activités pour la vidéo : 5051387-sd_640_360_25fps.mp4

	dancing ballet                            51.02%
	yoga                                       8.00%
	ice skating                                5.39%
	cartwheeling                               4.80%
	somersaulting                              3.47%

top-5 activit

## Références

Librairie MMAction : https://github.com/open-mmlab/mmaction2 <br>
Model Zoo : https://mmaction2.readthedocs.io/en/latest/model_zoo/recognition.html